<a href="https://colab.research.google.com/github/RC11-SkillsClass2022-23/LingyuZhai/blob/main/SkillClass1ZLY_video.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
! git clone https://github.com/kenshohara/video-classification-3d-cnn-pytorch.git

Cloning into 'video-classification-3d-cnn-pytorch'...
remote: Enumerating objects: 121, done.
remote: Total 121 (delta 0), reused 0 (delta 0), pack-reused 121
Receiving objects: 100% (121/121), 158.63 KiB | 19.83 MiB/s, done.
Resolving deltas: 100% (63/63), done.


In [ ]:
%cd video-classification-3d-cnn-pytorch/

/content/video-classification-3d-cnn-pytorch


In [ ]:
!pip install --upgrade moviepy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 388 kB 24.2 MB/s 
     |████████████████████████████████| 26.9 MB 1.2 MB/s 
  Created wheel for moviepy: filename=moviepy-1.0.3-py3-none-any.whl size=110742 sha256=aa42c279f2ad7b7b011e54858f5c36c2b7a8a770516705603d37daa186eba866
  Stored in directory: /root/.cache/pip/wheels/e4/a4/db/0368d3a04033da662e13926594b3a8cf1aa4ffeefe570cfac1
Successfully built moviepy
  Attempting uninstall: moviepy
    Found existing installation: moviepy 0.2.3.5
    Uninstalling moviepy-0.2.3.5:
      Successfully uninstalled moviepy-0.2.3.5


In [ ]:
import json
import os
from moviepy.editor import *
from moviepy import *
import shutil
import numpy as np

In [ ]:
def loadVideosToInfile(folder):
  videos = os.listdir(folder)
  with open('input', 'w') as inputfile:
    for v in videos:
      if v.split('.')[-1] == 'mp4':
        inputfile.write(v+'\n')

In [ ]:
def readAllOutput(outputFolder):
  dictionaries = {}
  output_files = os.listdir(outputFolder)
  print(output_files)
  for f in output_files:
    if f.split('.')[-1] == 'json':
      file = open(os.path.join(outputFolder, f))
      segments = json.load(file)
      for s in segments:
        dictionaries[s['video']] = s
  return dictionaries
dicts = readAllOutput('/content/drive/MyDrive/output')
dicts.keys()

['.ipynb_checkpoints', 'output2212111932.json']


dict_keys(['Althamer-Pawel_Africa_2009.mp4', 'Anger-Kenneth-Eaux-DArtifice_1953.mp4', 'Anger-Kenneth_Scorpio-Rising_1963.mp4', 'Angerame-Dominic_Consume.mp4', 'Antin-Eleanor_Archives.mp4', 'Arcangel-Cory_I-Shot-Andy-Warhol_2002.mp4', 'Arcangel-Cory_Naptime_2002.mp4', 'Arcangel-Cory_Beach-Boys-Geto-Boys.mp4', 'frame-057878.mp4'])

In [ ]:
def searchForMatch(keyFilmName, featureDictionary, frame = None, fps = 25, nBestMatches = 1):
  fragments = []
  keyClips = featureDictionary[keyFilmName]['clips']
  print(keyClips[0].keys())

  keyFeatures = []
  for c in keyClips:
    keyFeatures.append(np.array(c['segment']))
  if frame:
    ft = 16/fps
    sf = int(frame[0]/ft)
    ef = int(min(frame[1]/ft, len(keyFeatures)-1))
    keyFeatures = keyFeatures[sf:ef]
  for film in featureDictionary.keys():
    if not film == keyFilmName:
      filmClips = featureDictionary[film]['clips']
      filmFeatures = []
      for c in filmClips: 
        filmFeatures.append(np.array(c['segment']))
      for i in range(len(filmFeatures)-len(keyFeatures)):
        distance = 0
        for j in range(len(keyFeatures)):
          d = np.linalg.norm(filmFeatures[i+j]-keyFeatures[j])
          distance += d 
        distance = distance/len(keyFeatures)
        a = fragmentsExists(fragments, [film, i, len(keyFeatures), distance])
        if a: 
          fragments = a
        elif len(fragments) < nBestMatches:
          fragments.append([film, i, len(keyFeatures), distance])
          fragments.sort(key = lambda x : x[-1])
        elif distance < fragments[-1][-1]:
          fragments.pop()
          fragments.append([film, i, len(keyFeatures), distance])
          fragments.sort(key = lambda x : x[-1])
  return fragments                              

In [ ]:
def fragmentsExists(fragments, nf):
  for f in fragments:
    r = range(nf[1], nf[1]+nf[2])
    if f[0] == nf[0] and (f[1] in r or f[1]+f[2] in r):
      if f[-1] > nf[-1]:
        fragments.remove(f)
        fragments.append(nf)
        fragments.sort(key = lambda x : x[-1])
      return fragments
  return False

In [ ]:
def extractFragment(fragment, filmFolder):
  filmFileName = fragment[0]
  start = fragment[1]
  nrClips = fragment[2]

  film = VideoFileClip(os.path.join(filmFolder, filmFileName))
  tsfps = film.fps
  tsFrameLength = 1/tsfps

  nrFrames = nrClips * 16
  startFrame = start * 16

  startTime = startFrame * tsFrameLength
  endTime = startTime + nrFrames * tsFrameLength  

  filmFragment = film.subclip(startTime, endTime)

  return filmFragment 

In [ ]:
loadVideosToInfile('/content/drive/MyDrive/ScrapedVideos')

In [ ]:
! python main.py --input input --video_root /content/drive/MyDrive/ScrapedVideos --output /content/drive/MyDrive/output/output2212122338.json --model /content/drive/MyDrive/resnet-34-kinetics-cpu.pth --model_depth 34 --no_cuda --mode score #--resnet_shortcut A


loading model /content/drive/MyDrive/resnet-34-kinetics-cpu.pth
/content/drive/MyDrive/ScrapedVideos/frame-057878.mp4
ffmpeg version 3.4.11-0ubuntu0.1 Copyright (c) 2000-2022 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvorb

In [ ]:
input_films_processed = os.listdir('/content/drive/MyDrive/ScrapedVideos')
for file in input_films_processed:
  try:
    shutil.move(os.path.join('/content/drive/MyDrive/ScrapedVideos',file),'/content/drive/MyDrive/processed_films')
  except:
    print(file + ' not moved')

In [ ]:
dicts = readAllOutput('/content/drive/MyDrive/output')
dicts.pop('video3.mp4', None)

['.ipynb_checkpoints', 'output2212122338.json']


In [ ]:
dicts.keys()

dict_keys(['frame-057878.mp4', 'Askevold-David_TWO_HANKS.mp4', 'Atkins-Ed_Material-Witness_2012-SM.mp4', 'Atkins-Ed_Delivery_To_The_Following_Recipient_Failed_Permanently_2011_.mp4', 'Averty-Jean-Christophe_Alfred-Jarry_La-chanson-du-decervelage.mp4', 'Baillie-Bruce_Mr-Hayashi_1961.mp4', 'Baldessari-John_Title_1971.mp4'])

In [ ]:
keyName = 'frame-057878.mp4'
s = 0
d = 8

fragment = searchForMatch(keyName, dicts, frame = [s, s+d], nBestMatches = 100)

dict_keys(['segment', 'label', 'scores'])


In [ ]:
fragment

[['Askevold-David_TWO_HANKS.mp4', 0, 12, 0.0],
 ['Atkins-Ed_Material-Witness_2012-SM.mp4', 0, 12, 0.0],
 ['Atkins-Ed_Delivery_To_The_Following_Recipient_Failed_Permanently_2011_.mp4',
  0,
  12,
  0.0],
 ['Averty-Jean-Christophe_Alfred-Jarry_La-chanson-du-decervelage.mp4',
  0,
  12,
  0.0],
 ['Baillie-Bruce_Mr-Hayashi_1961.mp4', 0, 12, 0.0],
 ['Baldessari-John_Title_1971.mp4', 0, 12, 0.0],
 ['Askevold-David_TWO_HANKS.mp4', 13, 12, 294.1564209736038],
 ['Atkins-Ed_Material-Witness_2012-SM.mp4', 13, 12, 294.1564209736038],
 ['Atkins-Ed_Delivery_To_The_Following_Recipient_Failed_Permanently_2011_.mp4',
  13,
  12,
  294.1564209736038],
 ['Averty-Jean-Christophe_Alfred-Jarry_La-chanson-du-decervelage.mp4',
  13,
  12,
  294.1564209736038],
 ['Baillie-Bruce_Mr-Hayashi_1961.mp4', 13, 12, 294.1564209736038],
 ['Baldessari-John_Title_1971.mp4', 13, 12, 294.1564209736038],
 ['Askevold-David_TWO_HANKS.mp4', 26, 12, 588.3128419472076],
 ['Atkins-Ed_Material-Witness_2012-SM.mp4', 26, 12, 588.3128

In [ ]:
fragmentFilms = []
for f in fragment[64:68]:
  fragmentFilms.append(extractFragment(f, '/content/drive/MyDrive/processed_films'))

In [ ]:
final_clip = clips_array([fragmentFilms[0:2], fragmentFilms[2:4]])

In [ ]:
final_clip.ipython_display()

Moviepy - Building video __temp__.mp4.
MoviePy - Writing audio in __temp__TEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4


In [ ]:
final_clip.write_videofile("/content/drive/MyDrive/output_films/fragment116.mp4", audio_codec='aac')


Moviepy - Building video /content/drive/MyDrive/output_films/fragment116.mp4.
MoviePy - Writing audio in fragment116TEMP_MPY_wvf_snd.mp4


MoviePy - Done.
Moviepy - Writing video /content/drive/MyDrive/output_films/fragment116.mp4



Moviepy - Done !
Moviepy - video ready /content/drive/MyDrive/output_films/fragment116.mp4
